In [26]:
import csv
import datetime
import os
import numpy as np
import random
import math

from htm.bindings.sdr import SDR, Metrics
from htm.encoders.rdse import RDSE, RDSE_Parameters
from htm.encoders.date import DateEncoder
from htm.bindings.algorithms import SpatialPooler
from htm.bindings.algorithms import TemporalMemory
from htm.algorithms.anomaly_likelihood import AnomalyLikelihood 
#FIXME 代わりにTM.anomalyを使用しますが、 py.AnomalyLikelihoodよりも悪い結果になります
from htm.bindings.algorithms import Predictor

_INPUT_FILE_PATH ="gymdata.csv"

default_parameters = {
  # 2 つの（3 つの）エンコーダがあります: "value" (RDSE) & "time" (DateTime weekend, timeOfDay)
 'enc': {
      "value" :
         {'resolution': 0.88, 'size': 700, 'sparsity': 0.02},
      "time": 
         {'timeOfDay': (30, 1), 'weekend': 21}
 },
 'predictor': {'sdrc_alpha': 0.1},
 'sp': {'boostStrength': 3.0,
        'columnCount': 1638,
        'localAreaDensity': 0.04395604395604396,
        'potentialPct': 0.85,
        'synPermActiveInc': 0.04,
        'synPermConnected': 0.13999999999999999,
        'synPermInactiveDec': 0.006},
 'tm': {'activationThreshold': 17,
        'cellsPerColumn': 13,
        'initialPerm': 0.21,
        'maxSegmentsPerCell': 128,
        'maxSynapsesPerSegment': 64,
        'minThreshold': 10,
        'newSynapseCount': 32,
        'permanenceDec': 0.1,
        'permanenceInc': 0.1},
 'anomaly': {
   'likelihood': 
       {#'learningPeriod': int(math.floor(self.probationaryPeriod / 2.0)),
        #'probationaryPeriod': self.probationaryPeriod-default_parameters["anomaly"]["likelihood"]["learningPeriod"],
        'probationaryPct': 0.1,
        'reestimationPeriod': 100} #これらの設定は、NABからコピーされます
 }
}

def main(parameters=default_parameters, argv=None, verbose=True):
  if verbose:
    import pprint
    print("Parameters:")
    pprint.pprint(parameters, indent=4)
    print("")

  # 入力ファイルの読み込み.
  records = []
  with open(_INPUT_FILE_PATH, "r") as fin:
    reader = csv.reader(fin)
    headers = next(reader)
    next(reader)
    next(reader)
    for record in reader:
      records.append(record)

  # エンコーダーを作成します。 これらは入力データをバイナリ表現に変換します.
  dateEncoder = DateEncoder(timeOfDay= parameters["enc"]["time"]["timeOfDay"], 
                            weekend  = parameters["enc"]["time"]["weekend"]) 
  
  scalarEncoderParams            = RDSE_Parameters()
  scalarEncoderParams.size       = parameters["enc"]["value"]["size"]
  scalarEncoderParams.sparsity   = parameters["enc"]["value"]["sparsity"]
  scalarEncoderParams.resolution = parameters["enc"]["value"]["resolution"]
  scalarEncoder = RDSE( scalarEncoderParams )
  encodingWidth = (dateEncoder.size + scalarEncoder.size)
  enc_info = Metrics( [encodingWidth], 999999999 )

  # HTMを作る。 SpatialPoolerとTemporalMemoryと関連ツール.
  spParams = parameters["sp"]
  sp = SpatialPooler(
    inputDimensions            = (encodingWidth,),
    columnDimensions           = (spParams["columnCount"],),
    potentialPct               = spParams["potentialPct"],
    potentialRadius            = encodingWidth,
    globalInhibition           = True,
    localAreaDensity           = spParams["localAreaDensity"],
    synPermInactiveDec         = spParams["synPermInactiveDec"],
    synPermActiveInc           = spParams["synPermActiveInc"],
    synPermConnected           = spParams["synPermConnected"],
    boostStrength              = spParams["boostStrength"],
    wrapAround                 = True
  )
  sp_info = Metrics( sp.getColumnDimensions(), 999999999 )

  tmParams = parameters["tm"]
  tm = TemporalMemory(
    columnDimensions          = (spParams["columnCount"],),
    cellsPerColumn            = tmParams["cellsPerColumn"],
    activationThreshold       = tmParams["activationThreshold"],
    initialPermanence         = tmParams["initialPerm"],
    connectedPermanence       = spParams["synPermConnected"],
    minThreshold              = tmParams["minThreshold"],
    maxNewSynapseCount        = tmParams["newSynapseCount"],
    permanenceIncrement       = tmParams["permanenceInc"],
    permanenceDecrement       = tmParams["permanenceDec"],
    predictedSegmentDecrement = 0.0,
    maxSegmentsPerCell        = tmParams["maxSegmentsPerCell"],
    maxSynapsesPerSegment     = tmParams["maxSynapsesPerSegment"]
  )
  tm_info = Metrics( [tm.numberOfCells()], 999999999 )

  # セットアップ尤度（ゆうど）は、これらの設定が NAB
  anParams = parameters["anomaly"]["likelihood"]
  probationaryPeriod = int(math.floor(float(anParams["probationaryPct"])*len(records)))
  learningPeriod     = int(math.floor(probationaryPeriod / 2.0))
  anomaly_history = AnomalyLikelihood(learningPeriod= learningPeriod,
                                      estimationSamples= probationaryPeriod - learningPeriod,
                                      reestimationPeriod= anParams["reestimationPeriod"])

  predictor = Predictor( steps=[1, 5], alpha=parameters["predictor"]['sdrc_alpha'] )
  predictor_resolution = 1

  # データセット内のすべてのデータを反復処理し、入力と出力を記録します.
  inputs      = []
  anomaly     = []
  anomalyProb = []
  predictions = {1: [], 5: []}
  for count, record in enumerate(records):

    # 日付文字列をPythonの日付オブジェクトに変換する.
    dateString = datetime.datetime.strptime(record[0], "%m/%d/%y %H:%M")
    # データ値の文字列をfloatに変換.
    consumption = float(record[1])
    inputs.append( consumption )

    # エンコーダを呼び出して、各値のビット表現を作成します。 これらは SDR オブジェクトです.
    dateBits        = dateEncoder.encode(dateString)
    consumptionBits = scalarEncoder.encode(consumption)

    # これらのすべてのエンコーディングを 1 つの大きなエンコーディングに連結して、
    # 空間プーリング用に使用します.
    encoding = SDR( encodingWidth ).concatenate([consumptionBits, dateBits])
    enc_info.addData( encoding )

    # これは、以下の計算方法で作成されます
    # Spatial Poolerと同じ寸法でなければなりません
    activeColumns = SDR( sp.getColumnDimensions() )

    # 入力空間に対する空間プーリングアルゴリズムの実行.
    sp.compute(encoding, True, activeColumns)
    sp_info.addData( activeColumns )
    
    # SPSDR表示
    # print(activeColumns)
    re_activeColumns=activeColumns.dense.reshape(1,activeColumns.dense.shape[0])
    import matplotlib.pyplot as plt

    from IPython.display import display, clear_output
    %matplotlib inline
    
    clear_output(wait = True)
    plt.cla
    plt.imshow(re_activeColumns, cmap = "Blues", aspect=200)
    plt.pause(0.01)

    # アクティブなミニカラムに対してTemporal Memoryアルゴリズムを実行する.
    tm.compute(activeColumns, learn=True)
    tm_info.addData( tm.getActiveCells().flatten() )

    # 何が起こるかを予測し、今起こったことに基づいて予測器を訓練する.
    pdf = predictor.infer( tm.getActiveCells() )
    for n in (1, 5):
      if pdf[n]:
        predictions[n].append( np.argmax( pdf[n] ) * predictor_resolution )
      else:
        predictions[n].append(float('nan'))

    anomalyLikelihood = anomaly_history.anomalyProbability( consumption, tm.anomaly )
    anomaly.append( tm.anomaly )
    anomalyProb.append( anomalyLikelihood )

    predictor.learn(count, tm.getActiveCells(), int(consumption / predictor_resolution))


  # HTMの状態に関する情報と統計を印刷する.
  print("Encoded Input", enc_info)
  print("")
  print("Spatial Pooler Mini-Columns", sp_info)
  print(str(sp))
  print("")
  print("Temporal Memory Cells", tm_info)
  print(str(tm))
  print("")

  # 予測した入力と一致するように予測値をシフトする.
  for n_steps, pred_list in predictions.items():
    for x in range(n_steps):
        pred_list.insert(0, float('nan'))
        pred_list.pop()

  # 予測精度、Root-Mean-Squaredを計算します
  accuracy         = {1: 0, 5: 0}
  accuracy_samples = {1: 0, 5: 0}

  for idx, inp in enumerate(inputs):
    for n in predictions: # 予測された各[N]ステップ先の時間ステップ数について.
      val = predictions[n][ idx ]
      if not math.isnan(val):
        accuracy[n] += (inp - val) ** 2
        accuracy_samples[n] += 1
  for n in sorted(predictions):
    accuracy[n] = (accuracy[n] / accuracy_samples[n]) ** .5
    print("Predictive Error (RMS)", n, "steps ahead:", accuracy[n])


if __name__ == "__main__":
  main()

Parameters:
{   'anomaly': {   'likelihood': {   'probationaryPct': 0.1,
                                     'reestimationPeriod': 100}},
    'enc': {   'time': {'timeOfDay': (30, 1), 'weekend': 21},
               'value': {'resolution': 0.88, 'size': 700, 'sparsity': 0.02}},
    'predictor': {'sdrc_alpha': 0.1},
    'sp': {   'boostStrength': 3.0,
              'columnCount': 1638,
              'localAreaDensity': 0.04395604395604396,
              'potentialPct': 0.85,
              'synPermActiveInc': 0.04,
              'synPermConnected': 0.13999999999999999,
              'synPermInactiveDec': 0.006},
    'tm': {   'activationThreshold': 17,
              'cellsPerColumn': 13,
              'initialPerm': 0.21,
              'maxSegmentsPerCell': 128,
              'maxSynapsesPerSegment': 64,
              'minThreshold': 10,
              'newSynapseCount': 32,
              'permanenceDec': 0.1,
              'permanenceInc': 0.1}}

{5: [], 1: []}
{5: [], 1: []}
{5: [], 1: 

{5: [0.00010981006459318289, 0.00010981006459318289, 0.00010981006459318289, 0.00010981006459318289, 0.00031570489275015287, 0.7207208817176383, 0.0001098214346430055, 0.00010981006459318289, 0.00010981006459318289, 0.00010981320412402095, 0.00010981006459318289, 0.0001098079765613045, 0.00010981006459318289, 8.14266904812906e-05, 0.09834106924369718, 0.00010981006459318289, 0.00010981006459318289, 0.00013412231616757566, 0.00010981006459318289, 0.00010981006459318289, 0.00010981006459318289, 0.00010981006459318289, 0.00010978531337681943, 0.12385925645802312, 0.00013651539241542096, 0.00013651539241542096, 0.00013651561765067117, 0.00013651539241542096, 0.00013651087355866812, 0.00013651539241542096, 0.00013651539241542096, 0.00013651539241542096, 0.00013651539241542096, 0.00013651539241542096, 0.00013651539241542096, 0.00011921479879603767, 3.289952735096655e-08, 5.1620303764446604e-05, 0.00326553100896668, 0.00012735442754516275, 0.0001509032493197899, 0.018978756156057486, 0.000123

{5: [8.345094090277359e-05, 8.345094090277359e-05, 8.345094090277359e-05, 8.345094090277359e-05, 7.806958001649661e-05, 0.00023803806746271444, 8.331910055399942e-05, 9.189491929965335e-05, 8.345094090277359e-05, 8.343641131803895e-05, 9.218830314224279e-05, 8.232417203360953e-05, 8.864728026614155e-05, 7.566792533311225e-05, 9.120886981488498e-05, 8.344625120071939e-05, 8.345094090277359e-05, 8.282691000688233e-05, 8.345094090277359e-05, 8.345094090277359e-05, 9.215642183470774e-05, 8.345094090277359e-05, 9.803400840519518e-07, 0.00021513598179668758, 8.696077253359347e-05, 8.696077253359347e-05, 8.696355571422416e-05, 8.696077253359347e-05, 8.66913191198402e-05, 8.54563353500093e-05, 8.696077253359347e-05, 8.680018033752868e-05, 8.696077253359347e-05, 8.694382083975403e-05, 8.696077253359347e-05, 8.535721069170433e-05, 6.777468643737521e-05, 7.911447377055007e-05, 5.96508388294867e-05, 6.505112468324973e-05, 9.266859176417388e-05, 0.9940836872949362, 0.0008370228707213096, 0.00028746

{5: [0.0099509231015552, 0.0099509231015552, 0.0099509231015552, 0.0099509231015552, 0.004513244659797503, 0.305352349906974, 0.010278984731270969, 0.05027342633266128, 0.0099509231015552, 0.015279366985930375, 0.009779235096128411, 0.01489562574764767, 0.01203436184580174, 0.009052213162626659, 0.00494769163839009, 0.009386213803585605, 0.0099509231015552, 0.009363200301781569, 0.0099509231015552, 0.011918069999087315, 0.013240862832274481, 0.009944412842060841, 0.018600874213195326, 0.04238932507771167, 0.010232295816999219, 0.011829703756127477, 0.01050064054116816, 0.010232295816999219, 0.014932395241919444, 0.010417258332647988, 0.011304900477514621, 0.012604113784480602, 0.010232295816999219, 0.010213595783509834, 0.010232295816999219, 0.010847212004717093, 0.0009176995233781403, 0.001295756498913928, 0.0020718154374011685, 0.03171910347613015, 0.010303123264138429, 0.022978370297205265, 0.028688935789372788, 0.004657397025637612, 0.008148209043970409, 0.047379273471616995, 0.024

{5: [0.0007060171992394773, 0.0007060171992394773, 0.0007060171992394773, 0.0007060171992394773, 0.0005114328117843004, 0.008435792064833636, 0.0009157096541521377, 0.0007231751021401728, 0.0007060171992394773, 0.0007540105078228344, 0.0009126981076274883, 0.00027035549818528156, 0.0008051447917390075, 0.0005838396230773814, 0.0015830137180742484, 0.0007004430965550187, 0.0007060171992394773, 0.000704998661413625, 0.0007060171992394773, 0.0007471278336655448, 0.0010243768857726198, 0.0007060172001016737, 0.00021618442573753, 0.0006097251090328672, 0.0007185821811158696, 0.0007178216077304258, 0.0007090097698678347, 0.0007185821811158696, 0.0008626999284544805, 0.0007556234973997816, 0.0006381514736455615, 0.0007906530628015104, 0.0007185821811158696, 0.0009354033245055014, 0.0007185821811158696, 0.000526112314119321, 0.0014327088633110513, 0.0007442880748261792, 0.0013012681650704907, 0.9520040002151727, 0.00031599999381193424, 0.0012374143154149605, 0.0010503467150148678, 0.0007104030

...

{5: [7.209539811643097e-05, 7.209539811643097e-05, 7.209539811643097e-05, 7.209539811643097e-05, 8.601478044150518e-05, 4.625349886557759e-05, 4.369469346506418e-05, 6.538151791204356e-05, 5.8085102176190405e-05, 7.602065855633703e-05, 8.483373487693939e-05, 6.28070121413651e-05, 5.2528809328157215e-05, 5.8747016255864715e-05, 6.844832243438895e-05, 7.73887313377647e-05, 7.164352411269014e-05, 8.734897158512985e-05, 7.786937610373925e-05, 7.227975923718571e-05, 6.386055195172943e-05, 6.0741432115546876e-05, 9.8737935294302e-05, 4.876528845031922e-05, 7.144881488472548e-05, 8.544478465475537e-05, 6.908829256571731e-05, 7.203280219849767e-05, 7.314997669050994e-05, 7.090998408900506e-05, 6.920962870799676e-05, 0.00010636274349900734, 7.180772742966282e-05, 0.00013503615561878161, 0.00017719352071277807, 0.00015886917725170763, 1.538645658627151e-07, 0.00016154622360574816, 0.00026894494858043915, 0.0018506973689377216, 0.00012576650620938555, 0.0005383268393554846, 0.0002368488239752478,

{5: [6.987937438450408e-05, 6.987937438450408e-05, 6.987937438450408e-05, 6.987937438450408e-05, 8.35122715329514e-05, 4.0610918635393116e-05, 6.678765138739556e-05, 6.236344427615109e-05, 8.009948628453732e-05, 5.125409146020376e-05, 8.362539829477947e-05, 6.165223602046387e-05, 7.95742299802307e-05, 5.262776941093914e-05, 9.221740154927722e-05, 8.684420275150972e-05, 8.409592994011363e-05, 9.098034349451446e-05, 6.481916806162133e-05, 8.229758359130447e-05, 5.989452622551951e-05, 6.907624117043238e-05, 4.517923563695082e-06, 5.3258823683754494e-05, 7.051493678585392e-05, 6.960290735759436e-05, 7.073389716003893e-05, 7.027197477768453e-05, 5.6321893893523416e-05, 7.580196600495947e-05, 7.017584350822247e-05, 9.312001439688045e-05, 0.00011190013846837943, 7.858711687029077e-05, 0.00011959377281537535, 0.0003240388623455577, 6.010936992349453e-05, 0.00025889828970907777, 0.00018935464752879518, 4.0821295095977746e-07, 0.00042015752627293083, 0.00018387247494902056, 0.0001548923118817535

{5: [0.0008966227042513645, 0.0008966227042513645, 0.0008966227042513645, 0.0008966227042513645, 0.0009546872633066075, 0.000808698954244404, 0.000849354131833837, 0.0008864557003778229, 0.0007621627444528622, 0.0011288327930382386, 0.000865312517929488, 0.0010454225526907756, 0.0007704299166608081, 0.0006408698942597686, 0.00036308947542608184, 0.0009668199810153546, 0.0008968149390124538, 0.0009688558616448672, 0.00104284347539352, 0.0009566199557356708, 0.0009724289849602977, 0.8739961441934938, 0.0008541506754933928, 0.0010950451200198166, 0.0009132259768271059, 0.0017291587039545307, 0.0009779143706355284, 0.0009020582709214707, 0.003167133906748228, 0.002787446879516166, 0.002539082198535948, 0.0016084102551271629, 0.0018164105145292084, 0.0009704222023256508, 0.0014460608154067463, 0.0008249009099908058, 0.0038610607609046083, 0.0020912088864178777, 0.00036324514876627956, 0.0013956439662454526, 0.00033841318655054376, 0.00512297575898903, 0.0054793688527922995, 0.00727688563395

{5: [0.00038451204841057806, 0.00038451204841057806, 0.00038451204841057806, 0.00038451204841057806, 0.0002919795220686976, 0.0002707527814226026, 0.000468857782335039, 0.00046152282251534155, 0.00038660817481569256, 0.00034668717652199313, 0.00013651677662438572, 0.0011290201198036769, 0.0005680164678096206, 0.00046701087098596636, 0.0003204865058436446, 0.00034537293289127376, 0.0004049410662507758, 0.0003838306856914687, 0.0004132280377158513, 0.00034275409826322765, 0.0004564067449043659, 0.00039107664780177985, 0.00028770827890596247, 3.006676939066186e-05, 0.0009543864515997489, 8.690328590231569e-05, 0.00018060061841160846, 0.0003881066762997578, 0.0005689884780164763, 0.0011167152479010112, 0.0004038917563929617, 0.00043777401648280724, 0.0005046956997024739, 0.0024371631075800807, 0.0004504706797362301, 0.0002759890225932277, 0.0005848911490307407, 0.0006299808115713724, 0.0026795257342279092, 0.0009119536932811302, 0.0005061529417601107, 0.0008813197012998617, 0.0007432553282

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

